In [0]:
# read all csv files into a single RDD
import os.path

# reads all filenames that match the patter. Currently only two within the DBFS, 0819 and 0820
files = '/FileStore/tables/*_UkraineCombinedTweetsDeduped.csv'
tweets = spark.read.csv(files,header=True,sep=",",multiLine=True)

In [0]:
# remove columns not needed
dropped_tweets = tweets.drop("original_tweet_id", \
                            "original_tweet_userid", \
                            "original_tweet_username", \
                            "in_reply_to_status_id", \
                            "in_reply_to_user_id", \
                            "in_reply_to_screen_name", \
                            "quoted_status_id", \
                            "quoted_status_userid", \
                            "quoted_status_username", \
                            "extractedts")

dropped_tweets.show(1)

dropped_tweets.first()['text']

+---+---------+--------------+--------------------+------------+---------+---------+-----------+--------------------+-------------------+-------------------+------------+--------------------+--------------------+--------+-----------+--------------+----------+---------------+
|_c0|   userid|      username|            acctdesc|    location|following|followers|totaltweets|       usercreatedts|            tweetid|     tweetcreatedts|retweetcount|                text|            hashtags|language|coordinates|favorite_count|is_retweet|is_quote_status|
+---+---------+--------------+--------------------+------------+---------+---------+-----------+--------------------+-------------------+-------------------+------------+--------------------+--------------------+--------+-----------+--------------+----------+---------------+
|  0|173212647|JoeMokolobetsi|Yeshua Hamashiach...|Afrika Borwa|      219|      197|       4789|2010-07-31 19:09:...|1560416252937617411|2022-08-19 00:00:00|           0|De

In [0]:
# get only english tweets
english_tweets = dropped_tweets.filter(dropped_tweets.language == "en" )
english_tweets.show(5)

+---+-------------------+---------------+--------------------+------------+---------+---------+-----------+--------------------+-------------------+-------------------+------------+--------------------+--------------------+--------+-----------+--------------+----------+---------------+
|_c0|             userid|       username|            acctdesc|    location|following|followers|totaltweets|       usercreatedts|            tweetid|     tweetcreatedts|retweetcount|                text|            hashtags|language|coordinates|favorite_count|is_retweet|is_quote_status|
+---+-------------------+---------------+--------------------+------------+---------+---------+-----------+--------------------+-------------------+-------------------+------------+--------------------+--------------------+--------+-----------+--------------+----------+---------------+
|  0|          173212647| JoeMokolobetsi|Yeshua Hamashiach...|Afrika Borwa|      219|      197|       4789|2010-07-31 19:09:...|15604162529

In [0]:
# get only non-retweets
non_rt_tweets = english_tweets.filter(english_tweets.is_retweet == "False")
non_rt_tweets.show(5)

+---+-------------------+---------------+--------------------+------------+---------+---------+-----------+--------------------+-------------------+-------------------+------------+--------------------+--------------------+--------+-----------+--------------+----------+---------------+
|_c0|             userid|       username|            acctdesc|    location|following|followers|totaltweets|       usercreatedts|            tweetid|     tweetcreatedts|retweetcount|                text|            hashtags|language|coordinates|favorite_count|is_retweet|is_quote_status|
+---+-------------------+---------------+--------------------+------------+---------+---------+-----------+--------------------+-------------------+-------------------+------------+--------------------+--------------------+--------+-----------+--------------+----------+---------------+
|  0|          173212647| JoeMokolobetsi|Yeshua Hamashiach...|Afrika Borwa|      219|      197|       4789|2010-07-31 19:09:...|15604162529

In [0]:
# get average number of tweets per day from each user

from pyspark.sql.functions import col, to_date
from pyspark.sql.window import Window
from pyspark.sql import functions as F

# make copy of dataframe and convert each tweet created time stamp into a time stamp object
df = non_rt_tweets
df = df.withColumn("date", to_date(col("tweetcreatedts")))

# create window partitioned by user and ordered by date
window = Window.partitionBy("username").orderBy("date")

# Calculate the number of tweets per day for each user
df = df.withColumn("daily_tweet_count", F.count("text").over(window))

# Calculate the average number of tweets per day for each user
avg_tweet_volume = df.groupBy("username").agg(
    F.avg("daily_tweet_count").alias("avg_tweets_per_day")
)

#result_df.show()
avg_tweet_volume.sample(0.5).show()


+---------------+------------------+
|       username|avg_tweets_per_day|
+---------------+------------------+
|       09amarix|               1.0|
|      0_weimar2|               1.0|
|       1AmyChew|               8.0|
|    1taiwantalk|               1.0|
|    23idiocracy|               1.0|
|   247ChinaNews|               3.0|
|    2Freelancer|               1.0|
|   2ironichna4u|               1.0|
| 317Kaitlynn317|               1.5|
|     3DTechPrep|               1.0|
|         3dKan3|               1.5|
|    4HumanUnity|               1.0|
|4chan_Soc__Leak|               1.0|
|      50YOFrosh|               1.0|
|        5tuxnet|               2.0|
|      64BakerSt|               1.0|
|    77WABCradio|               1.0|
|     8tracBrown|               1.0|
|       93nights|               1.0|
|       99erNews|               4.0|
+---------------+------------------+
only showing top 20 rows



In [0]:
%sh pip install textblob

You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-5429fe39-255a-4d21-b0ad-39592e1a9b5f/bin/python -m pip install --upgrade pip' command.


In [0]:
# # calculate average sentiment for each user

# from pyspark.sql.functions import col, udf
# from pyspark.sql.types import FloatType
# from textblob import TextBlob

# # pass this function to the tweet column
# def analyze_sentiment(tweet):
#     analysis = TextBlob(tweet)
#     return analysis.sentiment.polarity

# # Register the sentiment analysis function as a Spark UDF
# sentiment_analysis_udf = udf(analyze_sentiment, FloatType())

# # Apply sentiment analysis to each tweet and create a new column
# df = df.withColumn("sentiment_score", sentiment_analysis_udf(col("text")))

# # Calculate the average sentimentality for each user
# avg_tweet_sentimentality = df.groupBy("username").agg(
#     F.avg("sentiment_score").alias("avg_sentimentality")
# )

# avg_tweet_sentimentality.show()

+---------------+--------------------+
|       username|  avg_sentimentality|
+---------------+--------------------+
|ArthurM40330824|0.015348638807024275|
|         radezz|-0.01547618742500...|
|    Readone_001|              -0.125|
|     sunnypeony|  -0.550000011920929|
|  thetribunechd|-0.02500000037252903|
|       yugan___|0.022975646345964017|
| bloomsbury1918|-0.03951785632719596|
|    pratik_dhal| 0.03333333507180214|
|     EMBUkraine|-0.01500000059604...|
|      ETTelecom|                 0.0|
|        Trontir| 0.19270833395421505|
|    revishvilig| 0.07142857302512441|
|        WebVixn|-0.04374999925494194|
|  f_o_r_Ukraine|-0.00154735900562...|
|madeleinemaste4| 0.29121121764183044|
|   ChrishaModis| 0.33312290410200757|
|      godabalta|                 0.0|
|UkraineNowMedia|                 0.0|
|   jay_dee_akaa|  0.6000000238418579|
|      Hainanftp| 0.07500000298023224|
+---------------+--------------------+
only showing top 20 rows



In [0]:
from pyspark.sql.functions import col, udf, to_date
from pyspark.sql.types import FloatType
from textblob import TextBlob
from pyspark.sql.window import Window
from pyspark.sql import functions as F

# get average number of tweets per day from each user

# make copy of dataframe and convert each tweet created time stamp into a time stamp object
df = non_rt_tweets
df = df.withColumn("date", to_date(col("tweetcreatedts")))

# create window partitioned by user and ordered by date
window = Window.partitionBy("username").orderBy("date")

# Calculate the number of tweets per day for each user
df = df.withColumn("daily_tweet_count", F.count("text").over(window))


# calculate average sentiment for each user

# pass this function to the tweet column
def analyze_sentiment(tweet):
    analysis = TextBlob(tweet)
    return analysis.sentiment.polarity

# Register the sentiment analysis function as a Spark UDF
sentiment_analysis_udf = udf(analyze_sentiment, FloatType())

# Apply sentiment analysis to each tweet and create a new column
df = df.withColumn("sentiment_score", sentiment_analysis_udf(col("text")))


# Calculate the average sentimentality for each user and the average number of tweets per day
avg_tweet_sentimentality_and_volume = df.groupBy("username").agg(
    F.avg("sentiment_score").alias("avg_sentimentality"),
    F.avg("daily_tweet_count").alias("avg_tweets_per_day")

)

#result_df.show()
avg_tweet_sentimentality_and_volume.show()

+--------------+--------------------+------------------+
|      username|  avg_sentimentality|avg_tweets_per_day|
+--------------+--------------------+------------------+
|      01_coins| -0.4000000059604645|               1.0|
|      09amarix|  0.3928571343421936|               1.0|
|     0_weimar2|                 0.0|               1.0|
|    0xdefinews|                 0.0|               3.0|
|        1860rm|                 0.0|               2.0|
|      1AmyChew| 0.06062499957624823|               8.0|
|  1ghostofKiev| 0.15000000596046448|               1.0|
|   1taiwantalk|                 0.0|               1.0|
|   23idiocracy|                 0.0|               1.0|
|  247ChinaNews| 0.43939393758773804|               3.0|
|   2Freelancer|  0.4124999940395355|               1.0|
|          2emc| 0.09000000357627869|               1.0|
|  2ironichna4u|                 0.0|               1.0|
|317Kaitlynn317| 0.20909090340137482|               1.5|
|    3DTechPrep| 0.300000011920

In [0]:
# # Normalize following and followers
# from pyspark.sql.functions import col, mean, count

# # Make sure you operate on unique users, in case of duplicates get the average for the user
# df_unique_users = english_tweets.groupBy("username").agg(
#     mean("followers").alias("followers"),
#     mean("following").alias("following"),
#     count("username")
# )

# # Calculate the mean and stddev for followers and following
# followers_mean = df_unique_users.agg({"followers": "mean"}).collect()[0][0]
# followers_stddev = df_unique_users.agg({"followers": "stddev"}).collect()[0][0]
# following_mean = df_unique_users.agg({"following": "mean"}).collect()[0][0]
# following_stddev = df_unique_users.agg({"following": "stddev"}).collect()[0][0]

# # Calculate the z_scores for each entry
# df_unique_users = df_unique_users.withColumn("followers_zscore", (col("followers") - followers_mean) / followers_stddev)
# df_unique_users = df_unique_users.withColumn("following_zscore", (col("following") - following_mean) / following_stddev)

# # Calculate normalized values
# # 99.7% of the data lie within 3 standard deviations of the mean, these values will be between 0-100, outliers will be outside this range
# df_unique_users = df_unique_users.withColumn("followers_normalized", ((col("followers_zscore") + 3) / 6)*100)
# df_unique_users = df_unique_users.withColumn("following_normalized", ((col("following_zscore") + 3) / 6)*100)

# # Drop unnecessary columns
# df_normalized_follow = df_unique_users.drop("count(username)", "followers_zscore", "following_zscore", "followers", "following")

# # display(df_normalized_follow)

In [0]:
# from pyspark.sql.functions import col, when, expr, count, sum

# df_quote_percentage = english_tweets.groupBy("username").agg(sum((col("is_quote_status") == "True").cast("int")).alias("is_quote_status_true_count"), sum((col("is_quote_status") == "False").cast("int")).alias("is_quote_status_false_count"))
# df_quote_percentage = df_quote_percentage.withColumn("percentage_of_quotes", 100*(col("is_quote_status_true_count") / (col("is_quote_status_true_count") + col("is_quote_status_false_count"))))
# df_quote_percentage = df_quote_percentage.drop('is_quote_status_true_count', 'is_quote_status_false_count')
# # percentage of retweets of a user in comparison to total tweets of the user(including retweets)
# display(df_quote_percentage)

username percentage_of_quotes ArthurM40330824 0.0 radezz 71.42857142857143 Readone_001 0.0 sunnypeony 100.0 thetribunechd 0.0 yugan___ 3.7735849056603774 bloomsbury1918 0.0 pratik_dhal 0.0 EMBUkraine 0.0 ETTelecom 0.0 Trontir 50.0 revishvilig 0.0 WebVixn 100.0 f_o_r_Ukraine 5.405405405405405 madeleinemaste4 0.0 ChrishaModis 0.0 godabalta 0.0 UkraineNowMedia 0.0 jay_dee_akaa 0.0 Hainanftp 0.0 rendissimo 0.0 khalifa_sandy 0.0 fmod1 0.0 AmyAComm 0.0 JBelcourt73 0.0 hugandmun 0.0 mandisadriana 0.0 ua_propaganda 0.0 shake_jones 10.526315789473683 longterm_invest 0.0 Nigel_Pickover 0.0 Bollerette 0.0 Ayonadre 50.0 transporeon_ 100.0 wertheim24 0.0 Rachelpowell 100.0 cpappalardo80 0.0 cannabistest1 0.0 AndrewPro20 0.0 testosteroneous 0.0 iNtRoVeRt_Ed 100.0 JimSand90389874 0.0 LaylaBe4 50.0 JohnLee92461223 0.0 EconMcCausland 100.0 JamesAbbott2013 0.0 KatenaEmma 0.0 mrgouldplays 0.0 ailinon80 0.0 DownHooligan 0.0 basshall 0.0 IonFPS 0.0 SahraHawkins 0.0 DinnerGunga 0.0 lovetheUSofA 100.0 ROYA__Ro 100.0 BloggerTdj 0.0 pjmssea 0.0 mhereast 0.0 LTrotsky21 0.0 anntirrell 100.0 TWMCLtd 12.903225806451612 kworshie 0.0 CenturyCruises 0.0 yoflipper 0.0 CarlWomack13 0.0 Hillsider4Life 0.0 ho_sa_ga 100.0 Clifford_Cliff1 0.0 Anastas34617414 0.0 RobertR41182121 100.0 DrPatridge 0.0 SINCLAIRTAIT1 0.0 MoniqueCamarra 37.5 bmarcois 0.0 TanishiHina 0.0 brecordernews 0.0 Philheadlines 0.0 farrellgraymond 0.0 mortenoxe 0.0 yespunjab 0.0 Ngiruwo69035842 0.0 Jominee 100.0 peaceresearch22 0.0 RodrigueOssi 0.0 jvantill 0.0 ATam47967776 0.0 WickedWomenThe1 0.0 Holydazein 0.0 DDIndialive 0.0 TheHatefulDead 0.0 Lviv_IT_Cluster 0.0 LyinDonnaB 0.0 automatedcrypto 0.0 pardonsentients 0.0 MarketsRadio 0.0 reynah_john 0.0 EvanHandler 0.0 Florian_Vienna 50.0 JaredMay76 0.0 vijaykumar1305 0.0 MuttonXops 0.0 AleksandrLogv16 0.0 AutoPasComplet 0.0 AMRAADfdg 0.0 PissedOffAR15 0.0 sinardailymy 0.0 RossFeingold 0.0 swflwarrior 0.0 3DTechPrep 0.0 E_4_Jupiter 8.333333333333332 BilyanaLilly 40.0 theoverview_ 80.0 GeorgiaVasilio9 100.0 iamsanyuktaroy 0.0 stephen95s 0.0 BNNUkraine 0.0 MafiaMoolah81St 0.0 ippfen 0.0 TonyCoxTC 0.0 SneakerNation03 0.0 VoGushuley 100.0 volodymyr_ml 22.22222222222222 HimjaParekh 100.0 NYCREMilton 0.0 a24newsagencyEN 0.0 PaulHodls 0.0 Cinnamon_Roses 100.0 arifjamallodhi 0.0 Craft_Wolf_Expo 0.0 jacksquat212 0.0 UKRinCoE 0.0 VReekaaa 0.0 aaron_m_arnold 100.0 Winnie_Byanyima 50.0 Ivan_T_Herrmann 0.0 clubOmozambique 0.0 Pandy67Andy 0.0 FictionTarot 0.0 TuanmudaJul 0.0 andriy0210 0.0 wlj2100 0.0 WeiyanShi1 0.0 wonder_dat_ass 0.0 ukrbravery 0.0 Jhansigir1 0.0 stevenmyers007 0.0 robbyusea 100.0 stevie_wond3rs 0.0 xoxofarm 0.0 RealMiBaWi 100.0 Abdnys 0.0 garland_paige 100.0 jam_onlineradio 0.0 mustlovesnark 56.25 AsianTigersJp 72.07207207207207 salvashunfans 0.0 Okun0728 0.0 rn2kKC4Y7SseB5z 0.0 kiwi_astronaunt 0.0 BCNewsWire 0.0 lemondrop110 0.0 Niguskw 0.0 GannaPetrovaa 100.0 richarddorset 0.0 DavidBu85029668 0.0 prakashkotha007 0.0 Crypto10078552 0.0 Dyadya_Jackson 0.0 AboveHeerlen 0.0 Inglorious_Jay 0.0 Kalush_Original 0.0 GiftsUkraine 0.0 Supernetworks 0.0 swissbcuae 0.0 charluv2011 0.0 trforrus 0.0 radioukraine1 0.0 AliedeChibuzor2 0.0 AviationNews 0.0 Cath_Aarts 0.0 VandelayT 100.0 RLAnalytica 100.0 sriram2412 0.0 trikrapka 0.0 PaulSalopek 0.0 qwerty14117587 0.0 PatakotaV 0.0 _rgupta 0.0 wmagates 0.0 McDilyTv 0.0 justinpowellweb 0.0 chetan_manjesh 0.0 sdh_za 0.0 deepali_popli57 0.0 DavidCriekemans 0.0 QsystemsMS 0.0 PatrioticCity 0.0 Entropy1024 0.0 MrPopperP1 0.0 socializ3r 0.0 mnicoletos 100.0 IZdarkstranger 0.0 junglezcl 0.0 igorsushko 12.5 ActivistBowen2 0.0 lal_shiban 0.0 gulf_news 0.0 VoiceAllahabad 0.0 MeridionaliAura 21.052631578947366 GigRevolt 0.0 Rainbow_July 0.0 olhahere 0.0 Ukrinform_News 0.0 sotodogenzenji 0.0 THEEURASIATIMES 0.0 MineFieldBingo 0.0 IronEcon1 0.0 Badguychido 0.0 RahulDaveIndia 100.0 SustainableCap2 0.0 scottlambkin 0.0 VladDanGheorghe 0.0 ChinaCG_Muc 100.0 FellaShaggy 33.33333333333333 Zawya 0.0 Scrutinizr 0.0 Shabbadidit1

In [0]:
# Normalize following and followers
from pyspark.sql.functions import col, mean, count, sum, expr

# Make sure you operate on unique users, in case of duplicates get the average for the user
df_unique_users = english_tweets.groupBy("username", "usercreatedts").agg(
    sum((col("is_quote_status") == "True").cast("int")).alias("is_quote_status_true_count"),
    sum((col("is_quote_status") == "False").cast("int")).alias("is_quote_status_false_count"),
    mean("followers").alias("followers"),
    mean("following").alias("following"),
    count("username").alias("tweet_count"),
    (unix_timestamp(current_time) - unix_timestamp(expr("substring(usercreatedts, 1, 19)"))).cast(LongType()).alias("account_age")
)

# Calculate the mean and stddev for followers and following
followers_mean = df_unique_users.agg({"followers": "mean"}).collect()[0][0]
followers_stddev = df_unique_users.agg({"followers": "stddev"}).collect()[0][0]
following_mean = df_unique_users.agg({"following": "mean"}).collect()[0][0]
following_stddev = df_unique_users.agg({"following": "stddev"}).collect()[0][0]

# Calculate the mean and stddev for account age
account_age_mean = df_unique_users.agg({"account_age": "mean"}).collect()[0][0]
account_age_stddev = df_unique_users.agg({"account_age": "stddev"}).collect()[0][0]

# Calculate the z_scores for each entry
df_unique_users = df_unique_users.withColumn("followers_zscore", (col("followers") - followers_mean) / followers_stddev)
df_unique_users = df_unique_users.withColumn("following_zscore", (col("following") - following_mean) / following_stddev)

df_unique_users = df_unique_users.withColumn("account_age_zscore", (col("account_age") - account_age_mean) / account_age_stddev)

# Calculate normalized values
# 99.7% of the data lie within 3 standard deviations of the mean, these values will be between 0-100, outliers will be outside this range
df_unique_users = df_unique_users.withColumn("followers_normalized", ((col("followers_zscore") + 3) / 6)*100)
df_unique_users = df_unique_users.withColumn("following_normalized", ((col("following_zscore") + 3) / 6)*100)

df_unique_users = df_unique_users.withColumn("account_age_normalized", ((col("account_age_zscore") + 3) / 6)*100)

# Unique users
df_unique_users = df_unique_users.withColumn("percentage_of_quotes", 100*(col("is_quote_status_true_count") / (col("is_quote_status_true_count") + col("is_quote_status_false_count"))))

# Drop unnecessary columns
df_normalized_follow = df_unique_users.drop("followers_zscore", "following_zscore", "followers", "following", "is_quote_status_true_count", "is_quote_status_false_count", "usercreatedts", "account_age_zscore", "account_age")

display(df_normalized_follow)

username tweet_count followers_normalized following_normalized account_age_normalized percentage_of_quotes OnlyCurrentNews 14 49.09964943052008 48.46458398420296 30.672828898248007 0.0 khurtovynny 2 49.07789772317132 46.24626852184785 29.80004136281547 100.0 PeceKocovski 1 49.08897648456351 46.45723972768438 64.5125523120462 0.0 danger_gamer75 1 49.15039259258891 49.53450938523111 61.71903406123679 0.0 WIONews 3 75.3151128415422 46.27536799851495 51.56865644400711 0.0 BizAvon1 1 49.08056798873764 46.129870615179414 37.6782506927964 0.0 SueG907 2 50.12396005523766 92.25254113254641 69.84663380923234 50.0 Gjmelio 2 49.101646042463294 47.61151896881302 51.045001113380536 0.0 JimGoughTrans 5 49.1051117062834 47.244865562807455 53.47755910376822 20.0 ElAmerican_ 6 54.76457860064641 60.63151398035331 35.74066294813469 0.0 BNNChina 7 49.08988551113928 46.05712192351164 29.473345019714586 0.0 Abu4eb00H 1 49.07857949310315 46.08864635656768 31.372576576265942 0.0 VisitoryNews 7 49.08439888644981 46.19291948129149 31.028252589299832 0.0 DJGalbreath 1 49.32697100493206 53.135569622785795 69.49808790819759 0.0 CEIS24060800 4 49.14948356601314 46.19776939406934 35.956572028791975 0.0 ttindia 3 66.6627895747813 46.408740599905876 71.91271571714405 0.0 Matus_Blasko 1 49.08596533403127 47.832190000205266 64.10557812811334 100.0 Dudemei13798642 9 49.079728401691966 46.122595746012635 35.0235742465748 11.11111111111111 Alam_Chaudry 3 49.129996308795086 48.18623363298842 49.029769778326425 100.0 1CaroleBell 4 49.08607896235324 47.09500325797185 35.27358905999304 25.0 SneakerNation03 1 49.1378366630111 49.09559227883556 36.99226463239122 0.0 nazmariam_txt 1 49.07999984712779 46.16866991740223 29.66772486342741 100.0 EvensFoundation 2 49.10835011345959 47.24535055408525 54.733018910537936 0.0 WarWritings 2 49.12672949453842 51.86974238776657 30.850781698047985 0.0 fodderman1914 1 49.09585099804276 49.96372666607096 59.685507216347766 0.0 workersliberty 1 49.42696392826667 56.913651676732044 70.7712195978177 0.0 andrew14ad 2 49.18198126609689 51.35807658970325 77.73642058042917 50.0 MyBlog385 2 49.07880674974709 48.37174279674124 43.47318890898244 0.0 Goldbroker_com 1 49.57916906554702 47.30839942019731 67.69707546110925 0.0 leblorik 2 49.135649317813154 50.27897099663131 56.64495023928381 0.0 James__1818 1 49.08965825449533 48.20078337132197 39.367167479266804 0.0 UNHumanRightsEU 1 49.64228959840199 46.731259799632994 54.742037077063344 100.0 Opportu727272 1 49.07960214800089 46.5712126779639 30.287208202834652 0.0 MichelDKerrigan 1 50.459561304179424 103.17454470826782 41.25245453446024 0.0 thepenof 1 49.142609052533885 49.04466819466812 42.90405271814991 0.0 melindacoxhall 1 49.420941627202204 59.62960283232884 66.5878156206544 0.0 V_TBot 1 49.19504852312357 47.51937062603385 59.1868923588435 0.0 hornydyxovka 1 49.07818179397625 46.37236625407199 37.412552774925615 0.0 OriginsD 1 49.163459849615585 48.460253704937024 56.98958389914611 100.0 TheArsenalNote 1 49.18448108918025 46.86705735741283 67.39422426033782 0.0 KathySi25030648 1 49.1441430348805 50.15772317718502 32.97029365195261 0.0 Sleepin13217724 1 49.078011351493295 46.40631564351694 37.89477933879438 0.0 Joseph_Zernik 1 49.173743212753976 51.13255564553315 73.60380778830464 0.0 TDL_Coop 1 49.115281441099825 46.23171878351429 43.93676802706977 0.0 GeeDawg55975157 2 49.788671284181305 46.25839330379248 31.13548130290404 0.0 Archana73121785 2 49.088124272148725 46.05469696712272 35.90162644079095 0.0 AskRajjj 1 49.085340378260426 46.47178946601794 53.008566912237356 0.0 SAY590 2 49.07968736924237 46.171094873791155 29.570755203416514 0.0 valdet_b 1 49.11363383043124 46.280217911292816 76.27767670899594 0.0 BelovedAntioch 2 49.16990825688745 49.932202233014934 52.08014802964659 0.0 tamara_tamisa 5 49.08078388254939 46.19049452490256 30.871730559025707 0.0 hem_day 6 49.11141807815281 46.21231913240289 63.449526053190105 16.666666666666664 SpartanWarGames 1 49.084204095040725 46.3941908615723

In [0]:
# from pyspark.sql.functions import col, unix_timestamp, current_timestamp, expr
# from pyspark.sql.types import LongType

# current_time = current_timestamp()

# # Truncate the trailing 0s from the usercreatedts field
# df_dates_transformed = english_tweets.withColumn("usercreatedts_truncated", expr("substring(usercreatedts, 1, 19)"))

# df_account_age = df_dates_transformed.select("username", "usercreatedts_truncated").distinct().groupBy("username", "usercreatedts_truncated").agg(
#     (unix_timestamp(current_time) - unix_timestamp("usercreatedts_truncated")).cast(LongType()).alias("account_age")
# )
# # Calculate the mean and stddev for account age
# account_age_mean = df_account_age.agg({"account_age": "mean"}).collect()[0][0]
# account_age_stddev = df_account_age.agg({"account_age": "stddev"}).collect()[0][0]

# df_account_age = df_account_age.withColumn("account_age_zscore", (col("account_age") - account_age_mean) / account_age_stddev)
# df_account_age = df_account_age.withColumn("account_age_normalized", ((col("account_age_zscore") + 3) / 6)*100)
# df_account_age = df_account_age.drop("account_age_zscore")
# df_account_age = df_account_age.drop("usercreatedts_truncated", "account_age")
# # normalized account age
# # display(df_account_age)

In [0]:
# username_counts = english_tweets.groupBy("username").count()
# username_counts = username_counts.withColumnRenamed("count", "tweet_count")
# # username_counts.show()

In [0]:
# df_final_non_rt = avg_tweet_volume.join(avg_tweet_sentimentality, on="username", how="inner")
# df_final = df_final_non_rt.join(df_normalized_follow, on="username", how="left").join(df_quote_percentage, on="username", how="inner").join(df_account_age, on="username", how="inner").join(username_counts, on="username", how="inner")
df_final = avg_tweet_sentimentality_and_volume.join(df_normalized_follow, on="username", how="left")
display(df_final)

username avg_sentimentality avg_tweets_per_day tweet_count followers_normalized following_normalized account_age_normalized percentage_of_quotes 01_coins -0.4000000059604645 1.0 1 49.08090887370356 46.16139504823545 32.46763592202936 0.0 09amarix 0.3928571343421936 1.0 1 49.08130657283045 47.090153345194 30.698030519832415 0.0 0_weimar2 0.0 1.0 1 49.09585099804276 49.064067845779526 35.02266136468726 100.0 0xdefinews 0.0 3.0 3 49.100055245955694 46.105621051290164 67.93371264691504 0.0 1860rm 0.0 2.0 2 49.08306781182101 46.413590512683726 64.73736649184744 0.0 1AmyChew 0.06062499957624823 8.0 8 49.80504086431527 47.44904689075501 48.68301594040063 0.0 1ghostofKiev 0.15000000596046448 1.0 1 49.1874354255515 46.34569173379381 29.58938267030143 0.0 1taiwantalk 0.0 1.0 1 49.11011135245013 46.77733397102258 61.53601112245896 0.0 23idiocracy 0.0 1.0 1 49.08079524538159 46.188069568513626 38.594212184530754 0.0 247ChinaNews 0.43939393758773804 3.0 3 49.10607754702016 46.17836974295793 33.67074399434791 0.0 2Freelancer 0.4124999940395355 1.0 1 49.15738073439013 50.245021607186345 72.18420235562277 0.0 2emc 0.09000000357627869 1.0 1 49.22765985152929 52.699077472779166 78.93791332603112 0.0 2ironichna4u 0.0 1.0 1 49.59212269425172 48.268682150211895 49.26963322659912 0.0 317Kaitlynn317 0.20909090340137482 1.5 2 49.07778409484935 46.04257218517809 29.377108321748324 0.0 3DTechPrep 0.30000001192092896 1.0 1 49.10857737010353 48.78519786105307 60.820261885159745 0.0 3dKan3 0.22500000521540642 1.5 2 49.17283418617821 58.11521756744473 71.62143613955818 0.0 44Observer4 -1.0 1.0 1 49.07903400639103 46.43784007657298 32.714860495931305 0.0 4HumanUnity -0.03999999910593033 1.0 1 50.277926431508554 94.66294778313858 74.05082264478318 0.0 50YOFrosh 0.0 1.0 1 49.12119011384233 47.963137645207254 53.86882548406328 0.0 5tuxnet 0.25833334028720856 2.0 2 49.14584745971006 47.80309052353815 34.87651826138563 0.0 64BakerSt 0.4553571343421936 1.0 1 49.080113475449764 46.845232749912505 61.68429646842958 100.0 73RDARM 0.2750000059604645 1.5 2 49.093521617442356 48.385080056880334 64.4490014181233 0.0 77WABCradio 0.42500001192092896 1.0 1 50.4344494450238 47.73034183187039 72.98841595126781 0.0 7H2mBetXwVbzV8N 0.011363636702299118 2.3333333333333335 3 49.09480940509136 46.64557800722429 36.02090264855026 0.0 7News247 0.0 1.0 1 49.078238608137234 46.047422097955945 32.54848327118655 0.0 88TrueTrade88 0.0 1.0 1 49.078011351493295 46.09107131295661 29.664788734056785 0.0 8tracBrown 0.800000011920929 1.0 1 49.081931528601295 46.37479121046091 29.87846028807702 0.0 918101el 0.0 1.0 1 49.1035777239368 49.03496836911241 49.62707094410486 0.0 93nights 0.25 1.0 1 49.08124975866947 46.917981441580274 42.7768591591091 0.0 99erNews 0.0031250000465661287 4.0 4 49.07806816565427 46.4845204870598 29.446995599547183 0.0 A21 0.4749999940395355 1.0 1 55.34194304263544 47.06347882491582 75.90798621966198 0.0 AB1solution 0.23333333432674408 1.0 1 49.08318144014298 46.27294304212604 55.340511618803276 0.0 ABC38503156 0.0 1.0 1 49.07772728068836 46.05954687990057 29.4582163845278 0.0 ACAPSproject 0.09545454382896423 1.0 1 49.97840217479262 53.9382301875202 67.4152260324591 0.0 ACLEDINFO 0.15000000596046448 1.5 2 51.603287178979954 56.12796580672011 64.36158606161939 0.0 ADFCFUTUREFOREX 0.06818182021379471 1.0 1 49.175334009261576 46.04257218517809 69.66975789391009 0.0 AE_ValMan -0.04642857238650322 1.0 1 49.142154539246 52.541455307499 65.61827665623458 0.0 AIReDaily 0.20624999701976776 1.0 1 49.27254303870789 46.58818737268638 72.57576819981745 0.0 AK47319026 0.19374999403953552 1.0 1 49.0783522364592 46.04257218517809 39.72579416066431 0.0 ALDotNews 0.0 1.0 1 49.07846586478117 46.403890687128026 29.51208519782525 0.0 AMRAADfdg 0.037500000558793545 4.0 4 49.190602815026445 46.80703968678692 32.568206723252466 0.0 ANFTHONY_ 0.699999988079071 1.0 1 49.27822445480645 58.0606560486939 52.9353617105507 0.0 ANU_SDSC -0.25 1.0 1 49.454689238827626 46.58333745990853 50.2308071807261

In [0]:
map_column = create_map(*[col(column).alias(column) for column in ["avg_tweets_per_day","avg_sentimentality","tweet_count","followers_normalized","following_normalized","account_age_normalized","percentage_of_quotes"]])

In [0]:
# create key-value objects:  key is username, value is a tuple with info of each tweet
# turn the dataframe into an RDD into order to use map
user_tweets = non_rt_tweets.rdd.map(lambda x : ((x.username), \
                                                (x.acctdesc, \
                                                x.location, \
                                                x.following, \
                                                x.followers, \
                                                x.totaltweets, \
                                                x.usercreatedts, \
                                                x.text, \
                                                x.tweetcreatedts, \
                                                x.retweetcount, \
                                                x.hashtags, \
                                                x.favorite_count)))


# group all tweets by same account together
user_tweets_grouped = user_tweets.groupByKey()

for record in user_tweets_grouped.take(5):
    print("\nUser\n")
    print("Username: " + record[0])
    for tweet in record[1]:
        print("\nTweet:")
        print(tweet[6])